In [1]:
#|default_exp app

# Export instructions

As of 24.3.18 the way to export cells to a python script is:
1) pip install nbdev
2) Add "#|default_exp [file_name]" to the top of your notebook
3) Add "#|export" to the top of each cell you want to export
4) run:
```python
    import nbdev
    notebook_name = "lesson_2.ipynb"
    export_destination = "." # the root directory
    nbdev.export.nb_export(notebook_name, export_destination)
```

# Code

In [2]:
#|export
from fastai.vision.all import *
from fastai.collab import *

if os.path.isfile('export.pkl'):
    learn: Learner = load_learner('export.pkl')
else:
    path = untar_data(URLs.PETS)
    dls = ImageDataLoaders.from_name_re(path, get_image_files(path/'images'), pat='(.+)_\d+.jpg', item_tfms=Resize(460), batch_tfms=aug_transforms(size=224, min_scale=0.75))
    learn = vision_learner(dls, models.resnet50, metrics=accuracy)
    learn.fine_tune(1)
    learn.path = Path('.')
    learn.export()

/Users/charlesfeinn/miniforge-pypy3/envs/default/lib/python3.9/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: 'dlopen(/Users/charlesfeinn/miniforge-pypy3/envs/default/lib/python3.9/site-packages/torchvision/image.so, 0x0006): Symbol not found: __ZN3c1017RegisterOperatorsD1Ev
  Referenced from: <CC4BC91F-8B6A-3F9A-B9EB-A2B9D578E202> /Users/charlesfeinn/miniforge-pypy3/envs/default/lib/python3.9/site-packages/torchvision/image.so
  Expected in:     <B36C132B-E822-3FDA-9BEC-DD9DB8197D06> /Users/charlesfeinn/miniforge-pypy3/envs/default/lib/python3.9/site-packages/torch/lib/libtorch_cpu.dylib'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng` installed before building `torchvision` from source?
  warn(


In [3]:
#|export
dls: DataLoaders = learn.dls
labels = dls.vocab

def predict(image):
    image = PILImage.create(image)
    prediction, prediction_index, probabilities = learn.predict(image)
    return { labels[i]: float(probabilities[i]) for i in range(len(labels))}


In [4]:
%pip install gradio

Note: you may need to restart the kernel to use updated packages.


In [5]:
#|export
import gradio
interface = gradio.Interface(
    fn=predict, 
    inputs=gradio.Image(height=512, width=512), 
    outputs=gradio.Label(num_top_classes=3),
    title="Dog Breed Classifier",
    description="Upload a photo of a dog and we'll tell you the likely breeds",
    article="This is Roman, he's a Red Nosed Pitbull (aka. American Pit-Bull Terrier) from New Orleans.\n\nTo try out the classifier, tap on his image to load him into the input box above and then press submit.",
    examples=['roman.png']
)
interface.launch(share=True)

/Users/charlesfeinn/miniforge-pypy3/envs/default/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://95de38d55a9ae84b0c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


In [6]:
%pip install jupyterlab-quarto

Note: you may need to restart the kernel to use updated packages.


In [7]:
import nbdev

notebook_name = "lesson_2.ipynb"
export_destination = "." # the root directory
nbdev.export.nb_export(notebook_name, export_destination)